In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


These are the requirements

In [2]:
import pandas as pd
import numpy as np
import librosa 
from tensorflow.keras.layers import Dense, LSTM, Dropout
from tensorflow.keras.callbacks import ModelCheckpoint, EarlyStopping
from tensorflow.keras.utils import Sequence
from tensorflow.keras.models import Sequential
import tensorflow as tf

In [ ]:
device_name = tf.test.gpu_device_name()
if device_name != '/device:GPU:0':
  raise SystemError('GPU device not found')
print('Found GPU at: {}'.format(device_name))

SystemError: ignored

Download the Data/Unzip

In [3]:

!unzip '/content/drive/MyDrive/Colab/data zips/cv-valid-train.csv.zip' -d '/content/drive/MyDrive/Colab/BigProjekt/'

# large data might take a very very long time to unzip
!unzip '/content/drive/MyDrive/Colab/data zips/cv-valid-train.zip' -d '/content/'


Streaming output truncated to the last 5000 lines.
  inflating: /content/cv-valid-train/sample-114641.mp3  
  inflating: /content/cv-valid-train/sample-142812.mp3  
  inflating: /content/cv-valid-train/sample-185443.mp3  
  inflating: /content/cv-valid-train/sample-013489.mp3  
  inflating: /content/cv-valid-train/sample-024609.mp3  
  inflating: /content/cv-valid-train/sample-168863.mp3  
  inflating: /content/cv-valid-train/sample-070666.mp3  
  inflating: /content/cv-valid-train/sample-194236.mp3  
  inflating: /content/cv-valid-train/sample-079463.mp3  
  inflating: /content/cv-valid-train/sample-130662.mp3  
  inflating: /content/cv-valid-train/sample-022340.mp3  
  inflating: /content/cv-valid-train/sample-118655.mp3  
  inflating: /content/cv-valid-train/sample-132630.mp3  
  inflating: /content/cv-valid-train/sample-128703.mp3  
  inflating: /content/cv-valid-train/sample-153268.mp3  
  inflating: /content/cv-valid-train/sample-135425.mp3  
  inflating: /content/cv-valid-train/

In [4]:
metadata = pd.read_csv('/content/drive/MyDrive/Colab/BigProjekt/cv-valid-train.csv')
metadata.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 195776 entries, 0 to 195775
Data columns (total 8 columns):
 #   Column      Non-Null Count   Dtype  
---  ------      --------------   -----  
 0   filename    195776 non-null  object 
 1   text        195776 non-null  object 
 2   up_votes    195776 non-null  int64  
 3   down_votes  195776 non-null  int64  
 4   age         73768 non-null   object 
 5   gender      74059 non-null   object 
 6   accent      64711 non-null   object 
 7   duration    0 non-null       float64
dtypes: float64(1), int64(2), object(5)
memory usage: 11.9+ MB


Metadata creation/Processing part 1

In [5]:
# metadata.columns returns an array of the labels for each column
# metadata.drop gets rid of that column as we do not care about it
# These if statements check if a certain column has been dropped or not
# If it has not been dropped then it is dropped.

print(metadata.columns)

if 'text' in metadata.columns:
    metadata = metadata.drop(['text'], axis=1)
if 'up_votes' in metadata.columns:
    metadata = metadata.drop(['up_votes'], axis=1)
if 'down_votes' in metadata.columns:
    metadata = metadata.drop(['down_votes'], axis=1)
if 'age' in metadata.columns:
    metadata = metadata.drop(['age'], axis=1)
if 'accent' in metadata.columns:
    metadata = metadata.drop(['accent'], axis=1)
if 'duration' in metadata.columns:
    metadata = metadata.drop(['duration'], axis=1)

print(metadata.columns)

# The data is very large so we are only going to take a slice of the data

metadata = metadata[:70000]

print()
metadata.info()
print()

# The next step is to get rid of all rows that contain neither male or female
# in gender. This is accomplished with drop and the use of a loop. The pd.isnull
# checks to see if the what is stored in the tuple is not a number. If it is, 
# then we can not use it and drop that row. This does take a while as 
# the data is still quite large, should take around three minutes

for row in metadata.itertuples(True, None):
    if (pd.isnull(row[2]) or row[2] == 'other'):
      metadata = metadata.drop([row[0]])

metadata.info()

Index(['filename', 'text', 'up_votes', 'down_votes', 'age', 'gender', 'accent',
       'duration'],
      dtype='object')
Index(['filename', 'gender'], dtype='object')

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 70000 entries, 0 to 69999
Data columns (total 2 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   filename  70000 non-null  object
 1   gender    26442 non-null  object
dtypes: object(2)
memory usage: 1.1+ MB

<class 'pandas.core.frame.DataFrame'>
Int64Index: 26169 entries, 5 to 69994
Data columns (total 2 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   filename  26169 non-null  object
 1   gender    26169 non-null  object
dtypes: object(2)
memory usage: 613.3+ KB


Metadata processing part 2

In [6]:
# now the data must be trimmed so there is an equal amount of males and females.

metadata['gender'].value_counts()


# as you can see there are way more male voice samples then female voice samples
# another for loop will take care of this.

desiredNumberSample = 6542 # set to the number of females
numMaleSamples = 0 # tracks the amount of male samples iterated through

for row in metadata.itertuples(True, None):
  if (row[2] == 'male' and numMaleSamples >= desiredNumberSample):
    metadata = metadata.drop(row[0])
  if (row[2] == 'male' and numMaleSamples <= desiredNumberSample):
    numMaleSamples += 1

metadata['gender'].value_counts()


female    6542
male      6542
Name: gender, dtype: int64

In [7]:
# now the data is split into testing and training sets.

validTest = pd.DataFrame(columns=['filename','gender']) # this is where the test data will be stored
validTrain = pd.DataFrame(columns=['filename','gender']) # where train data is stored
validValidation = pd.DataFrame(columns=['filename','gender'])

# there are 13084 total samples. 10% would be around 1308 samples. This breaks 
# down into 654 male samples and 654 female samples. The rest are the testing
# samples
metadata.info()

desiredNumberSample = 1308
maleSamplesTest = 0
femaleSamplesTest = 0
maleSamplesValid = 0
femaleSamplesValid = 0

for row in metadata.itertuples(False, None):
    if (row[1] == 'male' and maleSamplesTest < (desiredNumberSample/2)):
      validTest.loc[len(validTest)] = row
      maleSamplesTest += 1
    elif (row[1] == 'female' and femaleSamplesTest < (desiredNumberSample/2)):
      validTest.loc[len(validTest)] = row
      femaleSamplesTest += 1
    elif (row[1] == 'male' and maleSamplesValid < (desiredNumberSample/2)):
      validValidation.loc[len(validValidation)] = row
      maleSamplesValid += 1
    elif (row[1] == 'female' and femaleSamplesValid < (desiredNumberSample/2)):
      validValidation.loc[len(validValidation)] = row
      femaleSamplesValid += 1
    else :
      validTrain.loc[len(validTrain)] = row



<class 'pandas.core.frame.DataFrame'>
Int64Index: 13084 entries, 5 to 69991
Data columns (total 2 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   filename  13084 non-null  object
 1   gender    13084 non-null  object
dtypes: object(2)
memory usage: 306.7+ KB


In [8]:
#small dataset
validTrain.info()
smallTrain = pd.DataFrame(columns=['filename','gender'])
smallValid = pd.DataFrame(columns=['filename','gender'])
# small dataset has only 200 males and 200 females :D
desiredNumSamples = 400
numOfMalesTrain = 0
numOfFemalesTrain = 0

numOfMalesValid = 0
numOfFemalesValid = 0

for row in validTrain.itertuples(False, None):
    if (row[1] == 'male' and numOfMalesTrain < 500):
      smallTrain.loc[len(smallTrain)] = row
      numOfMalesTrain += 1
    elif (row[1] == 'female' and numOfFemalesTrain < 500):
      smallTrain.loc[len(smallTrain)] = row
      numOfFemalesTrain += 1
    elif (row[1] == 'male' and numOfMalesValid < 100):
      smallValid.loc[len(smallValid)] = row
      numOfMalesValid += 1
    elif (row[1] == 'female' and numOfFemalesValid < 100):
      smallValid.loc[len(smallValid)] = row
      numOfFemalesValid += 1

smallTrain.info() 
smallValid.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 10468 entries, 0 to 10467
Data columns (total 2 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   filename  10468 non-null  object
 1   gender    10468 non-null  object
dtypes: object(2)
memory usage: 245.3+ KB
<class 'pandas.core.frame.DataFrame'>
Int64Index: 1000 entries, 0 to 999
Data columns (total 2 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   filename  1000 non-null   object
 1   gender    1000 non-null   object
dtypes: object(2)
memory usage: 23.4+ KB
<class 'pandas.core.frame.DataFrame'>
Int64Index: 200 entries, 0 to 199
Data columns (total 2 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   filename  200 non-null    object
 1   gender    200 non-null    object
dtypes: object(2)
memory usage: 4.7+ KB


In [9]:
# The data is preprocessed so now a data generator is needed to generate and load the data into batches for use.


class DataGenerator(Sequence):

    def __init__(self, batch_size, dataset, n_mfccs):
        self.batch_size = batch_size
        self.dataset = dataset
        self.n_mfccs = n_mfccs
        self.on_epoch_end()
        

    def __len__(self):
        """Denotes the number of batches per epoch
        :return: number of batches per epoch
        """
        return int(np.floor(len(self.dataset) / self.batch_size))

    def __getitem__(self, index):
        """Generate one batch of data
        :param index: index of the batch
        :return: x_batch and y_batch
        """
        # Initialization
        x_batch = np.empty((self.batch_size, self.n_mfccs))
        y_batch = np.empty((self.batch_size, 1))

        # Generate indexes of the batch
        indexes = self.indexes[index * self.batch_size : (index + 1) * self.batch_size]
        pos_in_array = 0
        # Generate data
        for i in indexes:
            x_batch[pos_in_array,] = self.generate_x(self.dataset.iloc[i][0])
            y_batch[pos_in_array,] = self.generate_y(self.dataset.iloc[i][1])
            pos_in_array += 1

        # Return batch data
        return x_batch, y_batch



    def on_epoch_end(self):
        """Shuffle indexes after each epoch
        """
        self.indexes = np.arange(len(self.dataset))
        np.random.shuffle(self.indexes)

    def generate_x(self, data_path):
      x, sr = librosa.load(data_path)
      mfccs = np.mean(librosa.feature.mfcc(y=x, sr=sr, n_mfcc=40).T, axis=0)
      return mfccs


    def generate_y(self, gender):
      label_to_int = {'male' : 1, 'female' : 0}
      return label_to_int[gender]


In [10]:
# testing the dataGenerator
batch_size_thing = 100
validTest.info()
validValidation.info()
train = DataGenerator(batch_size=batch_size_thing, dataset=validTrain, n_mfccs=40)
validate = DataGenerator(batch_size=batch_size_thing, dataset=validValidation, n_mfccs=40)
test = DataGenerator(batch_size=batch_size_thing, dataset=validTest, n_mfccs=40)

smolTrain = DataGenerator(batch_size=batch_size_thing, dataset=smallTrain, n_mfccs=40)
smolValid = DataGenerator(batch_size=batch_size_thing, dataset=smallValid, n_mfccs=40)
validTrain.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1308 entries, 0 to 1307
Data columns (total 2 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   filename  1308 non-null   object
 1   gender    1308 non-null   object
dtypes: object(2)
memory usage: 30.7+ KB
<class 'pandas.core.frame.DataFrame'>
Int64Index: 1308 entries, 0 to 1307
Data columns (total 2 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   filename  1308 non-null   object
 1   gender    1308 non-null   object
dtypes: object(2)
memory usage: 30.7+ KB
<class 'pandas.core.frame.DataFrame'>
Int64Index: 10468 entries, 0 to 10467
Data columns (total 2 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   filename  10468 non-null  object
 1   gender    10468 non-null  object
dtypes: object(2)
memory usage: 245.3+ KB


This is Not Done

In [11]:
def create_model(vector_length=40):
    model = Sequential()
    model.add(Dense(256, input_shape=(vector_length,)))
    model.add(Dropout(0.3))
    model.add(Dense(256, activation="relu"))
    model.add(Dropout(0.3))
    model.add(Dense(128, activation="relu"))
    model.add(Dropout(0.3))
    model.add(Dense(128, activation="relu"))
    model.add(Dropout(0.3))
    model.add(Dense(64, activation="relu"))
    model.add(Dropout(0.3))
    # one output neuron with sigmoid activation function, 0 means female, 1 means male
    model.add(Dense(1, activation="sigmoid"))
    # using binary crossentropy as it's male/female classification (binary)
    model.compile(loss="binary_crossentropy", metrics=["accuracy"], optimizer="adam")
    # print summary of the model
    model.summary()
    return model

In [ ]:
!mkdir checkpoints

# creates a directory to store weights /content/checkpoints 

woooo

In [12]:
# construct the model
model = create_model()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 dense (Dense)               (None, 256)               10496     
                                                                 
 dropout (Dropout)           (None, 256)               0         
                                                                 
 dense_1 (Dense)             (None, 256)               65792     
                                                                 
 dropout_1 (Dropout)         (None, 256)               0         
                                                                 
 dense_2 (Dense)             (None, 128)               32896     
                                                                 
 dropout_2 (Dropout)         (None, 128)               0         
                                                                 
 dense_3 (Dense)             (None, 128)               1

In [ ]:
device_name = tf.test.gpu_device_name()
if device_name != '/device:GPU:0':
  raise SystemError('GPU device not found')
print('Found GPU at: {}'.format(device_name))

Found GPU at: /device:GPU:0


In [13]:
#use this to load weights in google drive
model.load_weights('/content/drive/MyDrive/Colab/BigProjekt/weight/chkpoint/epoch001_loss0.477.hdf5')

In [ ]:

# define modelCheckpoint
model_checkpoint = ModelCheckpoint(filepath='/content/drive/MyDrive/Colab/BigProjekt/weight/chkpoint/epoch{epoch:03d}_loss{loss:.3f}.hdf5', verbose=1, save_best_only=False, mode='min', save_weights_only='true')
# define early stopping to stop training after 5 epochs of not improving
early_stopping = EarlyStopping(mode="min", patience=5, restore_best_weights=True)


epochs = 100
# train the model using the training set and validating using validation set
model.fit(x=train, epochs=epochs, validation_data=validate,
          callbacks=[model_checkpoint, early_stopping])

/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/cor

Epoch 1/100


/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/cor

  1/104 [..............................] - ETA: 1:18:04 - loss: 0.5133 - accuracy: 0.7900

/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/cor

...

/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/cor

 73/104 [====================>.........] - ETA: 26:27 - loss: 0.3742 - accuracy: 0.8523

/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/cor

 74/104 [====================>.........] - ETA: 25:36 - loss: 0.3744 - accuracy: 0.8526

/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/cor

In [ ]:
#use this to load weights in google drive
model.load_weights('/content/drive/MyDrive/Colab/BigProjekt/weight/epoch001_loss2.033.hdf5')

In [16]:
label_to_double = {'male' : 1.0, 'female' : 0.0}
double_to_label = {1.0 : 'male', 0.0 : 'female'}

batchNum = 0
totalGuess = 0
guessCorrect = 0
index = 0

while (batchNum <= 13):
  index = 0
  feature, label = test[batchNum]
  for i in feature:
    
    guess = 0.5
    print("actual:")
    print(double_to_label[list(label[index])[0]])
    testFeature = i.reshape(1,-1)
    result = model.predict(x=testFeature)
    print("result: ",result)
    if (result < .5):
      guess = 0.0
      print('guess: female')
    else:
      guess = 1.0
      print('guess: male')
    if (guess == list(label[index])[0]):
      guessCorrect += 1
    totalGuess += 1
    index += 1
    print(totalGuess)
    print(guessCorrect)
  batchNum += 1

print(guessCorrect/totalGuess)

/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/cor

actual:
female
result:  [[0.08297521]]
guess: female
1
1
actual:
female
result:  [[0.17616862]]
guess: female
2
2
actual:
male
result:  [[0.664079]]
guess: male
3
3
actual:
female
result:  [[0.14018649]]
guess: female
4
4
actual:
female
result:  [[0.04613054]]
guess: female
5
5
actual:
male
result:  [[0.79939413]]
guess: male
6
6
actual:
female
result:  [[0.581623]]
guess: male
7
6
actual:
female
result:  [[0.8651879]]
guess: male
8
6
actual:
female
result:  [[0.37914085]]
guess: female
9
7
actual:
female
result:  [[0.28518963]]
guess: female
10
8
actual:
female
result:  [[0.22864059]]
guess: female
11
9
actual:
female
result:  [[0.28418863]]
guess: female
12
10
actual:
female
result:  [[0.03863043]]
guess: female
13
11
actual:
female
result:  [[0.12620813]]
guess: female
14
12
actual:
male
result:  [[0.8522368]]
guess: male
15
13
actual:
male
result:  [[0.95690364]]
guess: male
16
14
actual:
male
result:  [[0.58347225]]
guess: male
17
15
actual:
female
result:  [[0.1647825]]
guess: fe

/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/cor

actual:
male
result:  [[0.81523937]]
guess: male
101
93
actual:
female
result:  [[0.2526777]]
guess: female
102
94
actual:
female
result:  [[0.1066927]]
guess: female
103
95
actual:
female
result:  [[0.2760933]]
guess: female
104
96
actual:
male
result:  [[0.67240095]]
guess: male
105
97
actual:
male
result:  [[0.67171144]]
guess: male
106
98
actual:
male
result:  [[0.8007703]]
guess: male
107
99
actual:
female
result:  [[0.30445856]]
guess: female
108
100
actual:
male
result:  [[0.8872786]]
guess: male
109
101
actual:
male
result:  [[0.5826564]]
guess: male
110
102
actual:
male
result:  [[0.74556]]
guess: male
111
103
actual:
male
result:  [[0.80797434]]
guess: male
112
104
actual:
female
result:  [[0.1117546]]
guess: female
113
105
actual:
female
result:  [[0.11184871]]
guess: female
114
106
actual:
female
result:  [[0.43847853]]
guess: female
115
107
actual:
female
result:  [[0.25363222]]
guess: female
116
108
actual:
male
result:  [[0.9298984]]
guess: male
117
109
actual:
female
re

/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/cor

...

actual:
male
result:  [[0.9467428]]
guess: male
1101
983
actual:
female
result:  [[0.05827832]]
guess: female
1102
984
actual:
male
result:  [[0.60471576]]
guess: male
1103
985
actual:
female
result:  [[0.19547182]]
guess: female
1104
986
actual:
female
result:  [[0.1814493]]
guess: female
1105
987
actual:
female
result:  [[0.404666]]
guess: female
1106
988
actual:
male
result:  [[0.776808]]
guess: male
1107
989
actual:
female
result:  [[0.11076838]]
guess: female
1108
990
actual:
female
result:  [[0.09973401]]
guess: female
1109
991
actual:
female
result:  [[0.02654567]]
guess: female
1110
992
actual:
male
result:  [[0.91574883]]
guess: male
1111
993
actual:
female
result:  [[0.3115359]]
guess: female
1112
994
actual:
male
result:  [[0.88683474]]
guess: male
1113
995
actual:
female
result:  [[0.09029216]]
guess: female
1114
996
actual:
female
result:  [[0.09295738]]
guess: female
1115
997
actual:
female
result:  [[0.17184797]]
guess: female
1116
998
actual:
male
result:  [[0.8855165]]

/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/cor

actual:
male
result:  [[0.19109932]]
guess: female
1201
1070
actual:
female
result:  [[0.05231649]]
guess: female
1202
1071
actual:
male
result:  [[0.90225196]]
guess: male
1203
1072
actual:
female
result:  [[0.06872663]]
guess: female
1204
1073
actual:
male
result:  [[0.45244473]]
guess: female
1205
1073
actual:
female
result:  [[0.17166206]]
guess: female
1206
1074
actual:
male
result:  [[0.5684596]]
guess: male
1207
1075
actual:
female
result:  [[0.32171926]]
guess: female
1208
1076
actual:
female
result:  [[0.09223697]]
guess: female
1209
1077
actual:
male
result:  [[0.8477218]]
guess: male
1210
1078
actual:
male
result:  [[0.916783]]
guess: male
1211
1079
actual:
female
result:  [[0.26139027]]
guess: female
1212
1080
actual:
female
result:  [[0.26899695]]
guess: female
1213
1081
actual:
female
result:  [[0.2223604]]
guess: female
1214
1082
actual:
female
result:  [[0.06849721]]
guess: female
1215
1083
actual:
female
result:  [[0.13492855]]
guess: female
1216
1084
actual:
male
resu

/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")
/usr/local/lib/python3.7/dist-packages/librosa/cor

actual:
male
result:  [[0.72453135]]
guess: male
1301
1159
actual:
male
result:  [[0.45561844]]
guess: female
1302
1159
actual:
female
result:  [[0.12453699]]
guess: female
1303
1160
actual:
female
result:  [[0.2990698]]
guess: female
1304
1161
actual:
male
result:  [[0.9262229]]
guess: male
1305
1162
actual:
male
result:  [[0.8956901]]
guess: male
1306
1163
actual:
female
result:  [[0.48109296]]
guess: female
1307
1164
actual:
female
result:  [[0.4923699]]
guess: female
1308
1165
actual:
female
result:  [[0.48706025]]
guess: female
1309
1166
actual:
female
result:  [[0.48713416]]
guess: female
1310
1167
actual:
male
result:  [[0.48714742]]
guess: female
1311
1167
actual:
female
result:  [[0.48705968]]
guess: female
1312
1168
actual:
male
result:  [[0.48716184]]
guess: female
1313
1168
actual:
female
result:  [[0.4870807]]
guess: female
1314
1169
actual:
female
result:  [[0.48721895]]
guess: female
1315
1170
actual:
female
result:  [[0.48724896]]
guess: female
1316
1171
actual:
male
re